In [ ]:
import numpy as np
from glob import glob
import cv2
import matplotlib.pyplot as plt
import os
from tqdm import tqdm
# Specify the root directory path
root_path = r'D:\dataFaces\cropped'

# Collect all the person names
dir_names = os.listdir(root_path)
person_names = [name.split("_")[-1].title() for name in dir_names]
n_individuals = len(person_names)

IMG_W, IMG_H, IMG_C = (224, 224, 3)
# Select all the file paths
filepaths = [path  for name in dir_names for path in glob(root_path +'/'+name + '/*')]
np.random.shuffle(filepaths)
print(f"Total number of images to be loaded : {len(filepaths)}")

# Create space for the images
all_images = np.empty(shape=(len(filepaths), IMG_W, IMG_H, IMG_C), dtype = np.float32)
all_labels = np.empty(shape=(len(filepaths), 1), dtype = np.int32)

# For each path, load the image and apply some preprocessing.
for index, path in tqdm(enumerate(filepaths), desc="Loading Data"):

    # Extract label
    label = [name[5:] for name in dir_names if name in path][0]
    label = person_names.index(label.title())

    # Load the Image
    image = plt.imread(path)

    # Resize the image
    image = cv2.resize(image, dsize = (IMG_W, IMG_H))

    # Convert image stype
    image = image.astype(np.float32)/255.0

    # Store the image and the label
    all_images[index] = image
    all_labels[index] = label

# Save images and labels as .npy files
np.save(r'D:/notebooks Lab 5 and 5/all_images.npy', all_images)
np.save(r'D:/notebooks Lab 5 and 5/all_labels.npy', all_labels)


Total number of images to be loaded : 17431


Loading Data: 17431it [05:13, 55.58it/s] 


In [ ]:

label_mapping = {index: name for index, name in enumerate(dir_names)}  # Map label (index) to folder name

# Save the label mapping as a .npy file
np.save(r'D:/notebooks Lab 5 and 5/label_mapping.npy', label_mapping)

In [2]:
from keras_facenet import FaceNet
import numpy as np
import os
import cv2

# Initialize FaceNet
face_embedder = FaceNet()

def get_face_embeddings(image_paths):
    embeddings = []
    for path in image_paths:
        img = cv2.imread(path)
        img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        embedding = face_embedder.embeddings([img_rgb])[0]
        embeddings.append(embedding)
    return np.array(embeddings)

# Use the previously collected filepaths
face_embeddings = get_face_embeddings(filepaths)

# Save embeddings to a .npy file
np.save(r'D:/notebooks Lab 5 and 5/face_embeddings.npy', face_embeddings)

# Alternatively, to save multiple variables (like filepaths if needed) use np.savez
# np.savez('face_embeddings.npz', embeddings=face_embeddings, filepaths=filepaths)



1/1 ━━━━━━━━━━━━━━━━━━━━ 3s 3s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 78ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 78ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 81ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 74ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 77ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 75ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 80ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 75ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 79ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 79ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 74ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 74ms/step
1/1 ━━━━━━━━━

In [1]:
import os
import numpy as np
from tensorflow.keras.preprocessing.image import img_to_array, load_img  # Adjust if using another framework
import json
from tensorflow.keras.models import load_model
# Assuming your model is already loaded as `model`
# and your input size for the model is (input_height, input_width, channels)

# Set the path to your main folder
main_folder_path =r'D:\dataFaces\cropped'  # Update this path to your main folder

# Define a function to extract embeddings
def get_embedding(model, image_path):
    img = load_img(image_path, target_size=(224, 224))  # Resize if necessary
    img_array = img_to_array(img) / 255.0  # Normalize if your model expects normalized data
    img_array = np.expand_dims(img_array, axis=0)  # Expand dimensions to match model input shape
    embedding = model.predict(img_array)
    return embedding.flatten()

# Dictionary to store average embeddings for each class
average_embeddings = {}
model = load_model(r'D:\MODELs\inception80%.h5') 
# Loop through each class folder
for class_folder in os.listdir(main_folder_path):
    class_path = os.path.join(main_folder_path, class_folder)
    
    # Ensure we're working with folders
    if os.path.isdir(class_path):
        embeddings = []
        
        # Loop through each image in the class folder
        for image_file in os.listdir(class_path):
            image_path = os.path.join(class_path, image_file)
            
            # Check if it's an image file (you can add more formats if needed)
            if image_file.lower().endswith(('.png', '.jpg', '.jpeg')):
                embedding = get_embedding(model, image_path)
                embeddings.append(embedding)
        
        # Compute the average embedding for the class
        if embeddings:  # Avoid empty folders
            average_embedding = np.mean(embeddings, axis=0)
            average_embeddings[class_folder] = average_embedding.tolist()  # Convert to list for JSON compatibility

# Save the average embeddings to a JSON file
output_file = "average_embeddings.json"
with open(output_file, 'w') as f:
    json.dump(average_embeddings, f)

print(f"Average embeddings saved to {output_file}")


1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 203ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 191ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 192ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 194ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 183ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 198ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 187ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 187ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 183ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 201ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 177ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 190ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 188ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 183ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 189ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 178ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 186ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 188ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 193ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 180ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 181ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 188ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 191ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 195ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 